In [1]:
# Notebook bazuje na 
# https://github.com/bentrevett/pytorch-sentiment-analysis/blob/master/3%20-%20Faster%20Sentiment%20Analysis.ipynb

In [2]:
#conda install torchtext -c pytorch
#conda install spacy
#python -m spacy download en

In [3]:
import torch
from torchtext import data
from torchtext import datasets

SEED = 1234

torch.manual_seed(SEED)
torch.backends.cudnn.deterministic = True

TEXT = data.Field(tokenize = 'spacy')
LABEL = data.LabelField(dtype = torch.float)

/media/kuba/ssd/anaconda3/envs/tau/lib/python3.8/site-packages/torchtext/data/field.py:150: UserWarning: Field class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)
/media/kuba/ssd/anaconda3/envs/tau/lib/python3.8/site-packages/torchtext/data/field.py:150: UserWarning: LabelField class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)


In [4]:
import random

train_data, test_data = datasets.IMDB.splits(TEXT, LABEL)

train_data, valid_data = train_data.split(random_state = random.seed(SEED))

/media/kuba/ssd/anaconda3/envs/tau/lib/python3.8/site-packages/torchtext/data/example.py:78: UserWarning: Example class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('Example class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.', UserWarning)


In [5]:
print(f'Number of training examples: {len(train_data)}')
print(f'Number of validation examples: {len(valid_data)}')
print(f'Number of testing examples: {len(test_data)}')

Number of training examples: 17500
Number of validation examples: 7500
Number of testing examples: 25000


In [6]:
print(vars(train_data.examples[0]))

{'text': ['...', 'through', 'the', 'similarly', 'minded', 'antics', 'of', 'Eric', 'Stanze', '.', 'A', 'not', '-', 'particularly', 'talented', 'director', 'has', 'helmed', 'a', 'not', '-', 'particularly', 'good', 'movie', ',', 'yet', 'I', 'still', 'found', 'myself', 'sitting', 'through', 'it', 'to', 'the', 'closing', 'credits', ',', 'if', 'for', 'nothing', 'more', 'than', 'to', 'see', 'what', 'happens', 'next.<br', '/><br', '/>A', 'rapist', 'escapes', 'from', 'prison', 'and', 'calls', 'up', 'his', 'old', 'flame', '.', 'After', 'capturing', 'her', '(', 'even', 'though', 'she', 'came', 'willingly', ')', 'and', 'threatening', 'her', 'into', 'having', 'sex', '(', 'another', 'event', 'she', 'was', 'also', 'willing', 'to', 'do', ')', 'he', 'reveals', 'that', 'he', 'has', 'kidnapped', 'three', 'guys', 'who', 'wronged', 'her', 'in', 'the', 'past', '.', 'He', 'then', 'decides', 'to', 'kill', 'her', '(', 'huh', '?', ')', 'but', 'is', 'foiled', 'and', 'dies', 'instead', '.', 'The', 'girl', "'s", '

In [7]:
MAX_VOCAB_SIZE = 25_000

TEXT.build_vocab(train_data, max_size = MAX_VOCAB_SIZE)

LABEL.build_vocab(train_data)

In [8]:
print(f"Unique tokens in TEXT vocabulary: {len(TEXT.vocab)}")
print(f"Unique tokens in LABEL vocabulary: {len(LABEL.vocab)}")

Unique tokens in TEXT vocabulary: 25002
Unique tokens in LABEL vocabulary: 2


In [9]:
print(TEXT.vocab.freqs.most_common(20))

[('the', 202389), (',', 192527), ('.', 165463), ('a', 109375), ('and', 109303), ('of', 100836), ('to', 93959), ('is', 76223), ('in', 61140), ('I', 54434), ('it', 53612), ('that', 49147), ('"', 44429), ("'s", 43357), ('this', 42421), ('-', 37080), ('/><br', 35367), ('was', 34848), ('as', 30439), ('with', 29967)]


In [10]:
print(TEXT.vocab.itos[:10])

['<unk>', '<pad>', 'the', ',', '.', 'a', 'and', 'of', 'to', 'is']


In [11]:
print(LABEL.vocab.stoi)

defaultdict(None, {'neg': 0, 'pos': 1})


In [12]:
BATCH_SIZE = 64

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

train_iterator, valid_iterator, test_iterator = data.BucketIterator.splits(
    (train_data, valid_data, test_data), 
    batch_size = BATCH_SIZE, 
    device = device)

/media/kuba/ssd/anaconda3/envs/tau/lib/python3.8/site-packages/torchtext/data/iterator.py:48: UserWarning: BucketIterator class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)


In [13]:
import torch.nn as nn
import torch.nn.functional as F

class FastText(nn.Module):
    def __init__(self, vocab_size, embedding_dim, output_dim, pad_idx):
        
        super().__init__()
        
        self.embedding = nn.Embedding(vocab_size, embedding_dim, padding_idx=pad_idx)
        
        self.fc = nn.Linear(embedding_dim, output_dim)
        
    def forward(self, text):
        
        #text = [sent len, batch size]
        
        embedded = self.embedding(text)
                
        #embedded = [sent len, batch size, emb dim]
        
        embedded = embedded.permute(1, 0, 2)
        
        #embedded = [batch size, sent len, emb dim]
        
        pooled = F.avg_pool2d(embedded, (embedded.shape[1], 1)).squeeze(1) 
        
        #pooled = [batch size, embedding_dim]
                
        return torch.sigmoid(self.fc(pooled))

In [14]:
INPUT_DIM = len(TEXT.vocab)
EMBEDDING_DIM = 100
OUTPUT_DIM = 1
PAD_IDX = TEXT.vocab.stoi[TEXT.pad_token]

model = FastText(INPUT_DIM, EMBEDDING_DIM, OUTPUT_DIM, PAD_IDX)

In [15]:
def count_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

print(f'The model has {count_parameters(model):,} trainable parameters')

The model has 2,500,301 trainable parameters


In [16]:
UNK_IDX = TEXT.vocab.stoi[TEXT.unk_token]

model.embedding.weight.data[UNK_IDX] = torch.zeros(EMBEDDING_DIM)
model.embedding.weight.data[PAD_IDX] = torch.zeros(EMBEDDING_DIM)

In [17]:
import torch.optim as optim

optimizer = optim.Adam(model.parameters())

In [18]:
criterion = nn.BCELoss()

model = model.to(device)
criterion = criterion.to(device)

In [19]:
def binary_accuracy(preds, y):
    """
    Returns accuracy per batch, i.e. if you get 8/10 right, this returns 0.8, NOT 8
    """

    #round predictions to the closest integer
    rounded_preds = torch.round(preds)
    correct = (rounded_preds == y).float() #convert into float for division 
    acc = correct.sum() / len(correct)
    return acc

In [20]:
def train(model, iterator, optimizer, criterion):
    
    epoch_loss = 0
    epoch_acc = 0
    
    model.train()
    
    for batch in iterator:
        
        optimizer.zero_grad()
        
        predictions = model(batch.text).squeeze(1)
        
        loss = criterion(predictions, batch.label)
        
        acc = binary_accuracy(predictions, batch.label)
        
        loss.backward()
        
        optimizer.step()
        
        epoch_loss += loss.item()
        epoch_acc += acc.item()
        
    return epoch_loss / len(iterator), epoch_acc / len(iterator)

In [21]:
def evaluate(model, iterator, criterion):
    
    epoch_loss = 0
    epoch_acc = 0
    
    model.eval()
    
    with torch.no_grad():
    
        for batch in iterator:

            predictions = model(batch.text).squeeze(1)
            
            loss = criterion(predictions, batch.label)
            
            acc = binary_accuracy(predictions, batch.label)

            epoch_loss += loss.item()
            epoch_acc += acc.item()
        
    return epoch_loss / len(iterator), epoch_acc / len(iterator)

In [22]:
import time

def epoch_time(start_time, end_time):
    elapsed_time = end_time - start_time
    elapsed_mins = int(elapsed_time / 60)
    elapsed_secs = int(elapsed_time - (elapsed_mins * 60))
    return elapsed_mins, elapsed_secs

In [23]:
N_EPOCHS = 15

best_valid_loss = float('inf')

for epoch in range(N_EPOCHS):

    start_time = time.time()
    
    train_loss, train_acc = train(model, train_iterator, optimizer, criterion)
    valid_loss, valid_acc = evaluate(model, valid_iterator, criterion)
    
    end_time = time.time()

    epoch_mins, epoch_secs = epoch_time(start_time, end_time)
    
    if valid_loss < best_valid_loss:
        best_valid_loss = valid_loss
        torch.save(model.state_dict(), 'model.pt')
    
    print(f'Epoch: {epoch+1:02} | Epoch Time: {epoch_mins}m {epoch_secs}s')
    print(f'\tTrain Loss: {train_loss:.3f} | Train Acc: {train_acc*100:.2f}%')
    print(f'\t Val. Loss: {valid_loss:.3f} |  Val. Acc: {valid_acc*100:.2f}%')

/media/kuba/ssd/anaconda3/envs/tau/lib/python3.8/site-packages/torchtext/data/batch.py:23: UserWarning: Batch class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)


Epoch: 01 | Epoch Time: 0m 3s
	Train Loss: 0.685 | Train Acc: 59.98%
	 Val. Loss: 0.625 |  Val. Acc: 68.93%
Epoch: 02 | Epoch Time: 0m 2s
	Train Loss: 0.639 | Train Acc: 73.45%
	 Val. Loss: 0.513 |  Val. Acc: 75.19%
Epoch: 03 | Epoch Time: 0m 2s
	Train Loss: 0.560 | Train Acc: 79.02%
	 Val. Loss: 0.453 |  Val. Acc: 80.60%
Epoch: 04 | Epoch Time: 0m 2s
	Train Loss: 0.482 | Train Acc: 83.41%
	 Val. Loss: 0.410 |  Val. Acc: 84.11%
Epoch: 05 | Epoch Time: 0m 2s
	Train Loss: 0.420 | Train Acc: 86.42%
	 Val. Loss: 0.407 |  Val. Acc: 86.05%
Epoch: 06 | Epoch Time: 0m 2s
	Train Loss: 0.372 | Train Acc: 88.33%
	 Val. Loss: 0.432 |  Val. Acc: 87.06%
Epoch: 07 | Epoch Time: 0m 2s
	Train Loss: 0.333 | Train Acc: 89.47%
	 Val. Loss: 0.459 |  Val. Acc: 87.87%
Epoch: 08 | Epoch Time: 0m 2s
	Train Loss: 0.303 | Train Acc: 90.54%
	 Val. Loss: 0.480 |  Val. Acc: 88.36%
Epoch: 09 | Epoch Time: 0m 2s
	Train Loss: 0.276 | Train Acc: 91.32%
	 Val. Loss: 0.499 |  Val. Acc: 88.69%
Epoch: 10 | Epoch Time: 0m 2

In [24]:
model.load_state_dict(torch.load('tut3-model.pt'))

test_loss, test_acc = evaluate(model, test_iterator, criterion)

print(f'Test Loss: {test_loss:.3f} | Test Acc: {test_acc*100:.2f}%')

Test Loss: 0.434 | Test Acc: 82.76%


# User Input

In [25]:
import spacy
nlp = spacy.load('en')

def predict_sentiment(model, sentence):
    model.eval()
    tokenized = [tok.text for tok in nlp.tokenizer(sentence)]
    indexed = [TEXT.vocab.stoi[t] for t in tokenized]
    tensor = torch.LongTensor(indexed).to(device)
    tensor = tensor.unsqueeze(1)
    prediction = model(tensor)
    return prediction.item()

An example negative review...

In [26]:
predict_sentiment(model, "This film is terrible")

8.701013030076865e-06

An example positive review...

In [27]:
predict_sentiment(model, "This film is great")

1.0